In [1]:
import sys, os
sys.path.insert(0, '/home/hossay/gaitanalysis/src/dev')

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="8"

import torch
import torch.nn as nn
import numpy as np
from torch.utils.data import DataLoader
import torchvision.transforms as TF
from utils.transforms import (
    Compose, ToTensor, MultiScaleRandomCrop, MultiScaleCornerCrop, Normalize,
    TemporalRandomCrop, TemporalCenterCrop, LoopPadding)
import models
from utils.generate_model import load_pretrained_ckpt, generate_backbone
from utils.mean import get_mean, get_std
import datasets.gaitregression
from collections import namedtuple
from itertools import chain
from sklearn.preprocessing import StandardScaler
from scipy.ndimage import zoom
import cv2
from tqdm import tqdm
import copy

Opt = namedtuple('opts', ['ckpt_dir', 'attention_str', 'model_arch', 'merge_type', 'arch', 'group_str', 'pretrain_epoch', 
                          'backbone', 'pretrained_path', 'sample_duration', 'sample_size', 'img_size', 
                          'raw_h', 'raw_w',
                          'load_pretrained',
                          'norm_value', 'mean_dataset', 'data_root'])

opt = Opt(ckpt_dir='../ckpt_repos', attention_str='NonAttentive',
          model_arch='AGNet',
          merge_type='',
          arch='r2plus1d_18-18',
          group_str='', 
          pretrain_epoch='160',
          backbone='r2plus1d_18',
          pretrained_path='',
          sample_duration=64,
          sample_size=112,
          img_size=144,
          raw_h=480, raw_w=640,
          load_pretrained=False,
          norm_value=255,
          mean_dataset='kinetics',
          data_root="/data/GaitData/RawFrames"
         )


"""
--dataset MulticamFD 
--backbone r2plus1d_18 
--model_depth 18 
--pretrained_path  
--input_file ../../preprocess/data/person_detection_and_tracking_results_drop-MulticamFD.pkl
--data_root /data/FallDownData/MulticamFD/video
--multi_gpu
--with_segmentation
--device_ids 0,1,2,3,4,5,6,7
--batch_size 64 
--learning_rate 1e-4 
--n_threads 8 
--mode cv 
--model_arch AGNet-pretrain 
--n_iter 20 
--n_folds 5 
--sample_duration 16
--enable_guide
"""

{"dataset": "Gaitparams_PD", 
 "input_file": "../../../preprocess/data/person_detection_and_tracking_results_drop-Gaitparams_PD.pkl",
 "target_file": "../../../preprocess/data/targets_dataframe-Gaitparams_PD.pkl",
 "log_dir": "./logs",
 "data_root": "/data/GaitData/CroppedFrameArrays",
 "video_home": "/data/GaitData/NPH_patients_analysis/Video_converted",
 "chunk_vid_home": "./video_chunks",
 "chunk_parts": 8,
 "meta_home": "/data/GaitData/NPH_patients_analysis/MetaData_converted",
 "darknet_api_home": "../../../preprocess/darknet",
 "target_columns": "all",
 "pretrained_path": "",
 "backbone": "r2plus1d_18",
 "model_depth": 18,
 "device_ids": "0",
 "segm_method": null,
 "segm_device": 9,
 "img_size": 144,
 "sample_size": 112,
 "raw_h": 480,
 "raw_w": 640,
 "sample_duration": 64,
 "maxlen": 300,
 "fps": 24,
 "delta": 6,
 "multi_gpu": true,
 "with_segmentation": true,
 "mode": "demo",
 "batch_size": 4,
 "n_iter": 100,
 "n_threads": 16,
 "CV": 5,
 "train_crop": "", 
 "learning_rate": 0.0001,
 "momentum": 0.9,
 "dampening": 0.9,
 "weight_decay": 0.001,
 "mean_dataset": "kinetics",
 "no_mean_norm": false,
 "std_norm": false,
 "norm_value": 255, 
 "nesterov": false,
 "lr_patience": 10,
 "max_gradnorm": 5.0,
 "checkpoint": 10,
 "ckpt_dir": "/data/GaitData/ckpt_dir",
 "test_epoch": "40",
 "pretrain_epoch": "160",
 "score_avg": false,
 "model_arch": "AGNet",
 "merge_type": "",
 "warm_start": false,
 "num_units": 256,
 "n_factors": 15,
 "n_groups": -1,
 "drop_rate": 0.0,
 "attention": false,
 "data_gen": false,
 "interval_sel": "", 
 "port": 5001,
 "load_pretrained": false}


# dataset statics
mean = get_mean(opt.norm_value, dataset=opt.mean_dataset)
std = get_std(opt.norm_value, dataset=opt.mean_dataset)

# target columns to eval
target_columns = ['Velocity', 'Cadence', 'Cycle Time(sec)/L', 'Cycle Time(sec)/R',
         'Stride Length(cm)/L', 'Stride Length(cm)/R', 'HH Base Support(cm)/L',
         'HH Base Support(cm)/R', 'Swing % of Cycle/L', 'Swing % of Cycle/R',
         'Stance % of Cycle/L', 'Stance % of Cycle/R', 'Double Supp % Cycle/L',
         'Double Supp % Cycle/R', 'Toe In / Out/L', 'Toe In / Out/R',
         'CV Stride Length/L', 'CV Stride Length/R',
         'CV Stride Time/L', 'CV Stride Time/R']


def get_mlist():
    
    """
        moduel List to register to forward hook  ####
    """
    
    bsm_seq = lambda prime, i : [f'{prime}.{branch}_layers.{i}' for branch in ['backbone', 'seg', 'matching' ]] 

    m_list = [ *list(chain(*[ bsm_seq('pretrained_agnet', i) for i in range(4)])),
              'pretrained_agnet.conv_1x1',
              'pretrained_agnet.fc',
              *list(chain(*[ bsm_seq('agnet', i) for i in range(4)])),
              'agnet.conv_1x1',
              'agnet.fc']
    return m_list

def get_activation(m_dict, activation_layer, activation='relu'):
    A_k = m_dict[activation_layer]
    
    # move CUDA tensor to CPU
    A_k = A_k.cpu()
            
    # remove batch dim
    conv_out = A_k.data[0].numpy()
    
    # average
    conv_out = np.mean(conv_out, axis=0)
            
    # upsample grad_cam
    temporal_ratio = 64 / conv_out.shape[0]
    spatial_ratio = 112 / conv_out.shape[1]
    
    conv_out = zoom(conv_out, (temporal_ratio, spatial_ratio, spatial_ratio))
    
    
    if activation=='relu':
        conv_out = np.maximum(conv_out, 0)
    elif activation=='sigmoid':
        conv_out = 1/(1 + np.exp(-x))

    conv_out = conv_out / conv_out.max((1,2))[:,None,None]
    
    return conv_out


def generate_grad_cam(m_dict, p_index, activation_layer):
    y_c = torch.cat((m_dict['pretrained_agnet.fc'], m_dict['agnet.fc']), 1)[0, p_index]
    A_k = m_dict[activation_layer]
            
    grad_val = torch.autograd.grad(y_c, A_k, retain_graph=True)[0].data
    
    # move CUDA tensor to CPU
    A_k = A_k.cpu()
    grad_val = grad_val.cpu()

    # remove batch dim
    conv_out = A_k.data[0].numpy()
    grad_val = grad_val[0].numpy()
    
    weights = np.mean(grad_val, axis=(1,2,3))
    #grad_cam = weights * conv_out
    
    grad_cam = np.zeros(dtype=np.float32, shape=conv_out.shape[1:])
    for k, w in enumerate(weights):
        grad_cam += w * conv_out[k]
        
    # upsample grad_cam
    temporal_ratio = 64 / grad_cam.shape[0]
    spatial_ratio = 112 / grad_cam.shape[1]
    
    grad_cam = zoom(grad_cam, (temporal_ratio, spatial_ratio, spatial_ratio))
    
    positive_grad_cam = np.maximum(grad_cam, 0)
    negative_grad_cam = np.maximum(-grad_cam, 0)
        
    positive_grad_cam = positive_grad_cam / positive_grad_cam.max((1,2))[:,None,None]
    negative_grad_cam = negative_grad_cam / negative_grad_cam.max((1,2))[:,None,None]
        
    return positive_grad_cam, negative_grad_cam

In [2]:
backbone = generate_backbone(opt)
pretrained_agnet = models.regression_model.AGNet_Mean(
                backbone, hidden_size=512, out_size=16, drop_rate=0.0, freeze=False)
pretrained_agnet = load_pretrained_ckpt(opt, pretrained_agnet)
net = models.regression_model.AGNet(
    pretrained_agnet,
    backbone, hidden_size=1024, out_size=4)

if torch.cuda.is_available():
    net.cuda()

# global vars
m_list = get_mlist()
m_dict = {}

def hook(m, inp, out):
    global m_list
    global m_dict
        
    layer_name = m_list.pop(0)
    m_dict[layer_name] = out

# register hook for activation visualization
net.pretrained_agnet[-1].fc.register_forward_hook(hook)
net.pretrained_agnet[-1].agnet.conv_1x1.register_forward_hook(hook)
for i in range(4):
    net.pretrained_agnet[-1].agnet.backbone[i].register_forward_hook(hook)
    net.pretrained_agnet[-1].agnet.matching_layers[i].register_forward_hook(hook)
    net.pretrained_agnet[-1].agnet.seg_layers[i].register_forward_hook(hook)

net.fc.register_forward_hook(hook)
net.conv_1x1.register_forward_hook(hook)
for i in range(4):
    net.agnet.backbone[i].register_forward_hook(hook)
    net.agnet.matching_layers[i].register_forward_hook(hook)
    net.agnet.seg_layers[i].register_forward_hook(hook)


Load pretrained model from ../ckpt_repos/NonAttentive_AGNet-pretrain_r2plus1d_18-18/save_160.pth...


In [3]:
def probe_forward_vals(net, img_tensor, m_dict, m_list):
    img_tensor = img_tensor[None, :]    
    
    with torch.no_grad():
        net.eval()
        out = net(img_tensor)
    
    m_list = get_mlist()
    
    return m_dict, m_list

In [4]:
spatial_transform = Compose(
            [
                TF.CenterCrop(opt.sample_size),
                ToTensor(opt.norm_value),
                Normalize(mean, std),
            ]
)

target_transform = StandardScaler()


# prepare dataset  (train/test split)
data = datasets.gaitregression.prepare_dataset(
    input_file="../../../preprocess/data/person_detection_and_tracking_results_drop.pkl",
    target_file="../../../preprocess/data/targets_dataframe.pkl",
    target_columns=target_columns,
    chunk_parts=8,
    target_transform=target_transform,
)

# test dataset
ds = datasets.gaitregression.GAITSegRegDataset(
            X=data["test_X"], y=data["test_y"], opt=opt, phase='test',
            spatial_transform=spatial_transform
        )

In [5]:
def denormalization(img, mean, std):
    return img.permute(1,2,0).numpy()*std + mean

def write_activation_video(net, ds, save_dir,
                           activation_layer='pretrained_agnet.conv_1x1'):
        
    os.system('mkdir -p {}'.format(save_dir))
    
    for i in tqdm(range(len(ds))):
        global m_dict
        global m_list
        
        img_tensor, mask_tensor, target, vid, _ = ds[i]

        if torch.cuda.is_available():
            img_tensor = img_tensor.cuda()

        m_dict, m_list = probe_forward_vals(net, img_tensor, m_dict, m_list)

        # get activation results
        activation_result = get_activation(m_dict, 
                                           activation_layer=activation_layer,
                                           activation='relu')

        out = cv2.VideoWriter(os.path.join(save_dir, vid+'.avi'),
                              cv2.VideoWriter_fourcc('M','J','P','G'), 
                              24.0, (112,112))

        # Move CUDA tensor to CPU
        img_tensor = img_tensor.cpu()

        for t in range(img_tensor.size(1)):
            img_ = np.uint8(255*denormalization(img_tensor[:,t], mean, std))
            heatmap_ = np.uint8(255*activation_result[t])
            heatmap_ = cv2.applyColorMap(heatmap_, cv2.COLORMAP_JET)
            frame = np.uint8(heatmap_*0.3 + img_*0.5)
            out.write(frame)

        out.release()
        

write_activation_video(net, ds, save_dir='/data/GaitData/ActivationMap_videos/AGNet',
                       activation_layer='pretrained_agnet.conv_1x1')

100%|██████████| 731/731 [12:03<00:00,  1.04it/s]


In [6]:
# T = 20

# p_index = 9
# print(target_columns[p_index])

# positive_grad_cam, negative_grad_cam = generate_grad_cam(m_dict, p_index=p_index, activation_layer='pretrained_agnet.conv_1x1')

# import matplotlib.pyplot as plt

# def denormalization(img, mean, std):
#     return img.permute(1,2,0).numpy()*std + mean

# fig, (ax1, ax2, ax3) = plt.subplots(1,3,figsize=(15,15))

# ax1.imshow(denormalization(img_tensor[:,T], mean, std))
# ax1.set_title('INPUT IMG')

# ax2.imshow(positive_grad_cam[T])
# ax2.set_title('Positive grad-CAM')

# ax3.imshow(negative_grad_cam[T])
# ax3.set_title('Negative grad-CAM')
# plt.show()

In [7]:
# convert *.avi -> *.mp4
!sh convert_video-AGNet.sh

ffmpeg version 2.8.15-0ubuntu0.16.04.1 Copyright (c) 2000-2018 the FFmpeg developers
  built with gcc 5.4.0 (Ubuntu 5.4.0-6ubuntu1~16.04.10) 20160609
  configuration: --prefix=/usr --extra-version=0ubuntu0.16.04.1 --build-suffix=-ffmpeg --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --cc=cc --cxx=g++ --enable-gpl --enable-shared --disable-stripping --disable-decoder=libopenjpeg --disable-decoder=libschroedinger --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmodplug --enable-libmp3lame --enable-libopenjpeg --enable-libopus --enable-libpulse --enable-librtmp --enable-libschroedinger --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --

frame=   64 fps=0.0 q=-1.0 Lsize=      19kB time=00:00:02.58 bitrate=  60.8kbits/s    
video:18kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 8.694207%
[libx264 @ 0x224be20] frame I:1     Avg QP:26.57  size:  1182
[libx264 @ 0x224be20] frame P:34    Avg QP:24.79  size:   415
[libx264 @ 0x224be20] frame B:29    Avg QP:28.46  size:    72
[libx264 @ 0x224be20] consecutive B-frames: 18.8% 59.4%  9.4% 12.5%
[libx264 @ 0x224be20] mb I  I16..4:  0.0% 87.8% 12.2%
[libx264 @ 0x224be20] mb P  I16..4:  2.1%  8.9%  0.4%  P16..4: 35.1% 25.9% 11.9%  0.0%  0.0%    skip:15.6%
[libx264 @ 0x224be20] mb B  I16..4:  0.1%  0.7%  0.1%  B16..8: 19.8%  4.4%  1.2%  direct: 3.8%  skip:70.0%  L0:29.6% L1:56.5% BI:13.9%
[libx264 @ 0x224be20] 8x8 transform intra:80.5% inter:67.5%
[libx264 @ 0x224be20] coded y,uvDC,uvAC intra: 63.9% 75.7% 41.8% inter: 20.5% 34.5% 6.6%
[libx264 @ 0x224be20] i16 v,h,dc,p: 36% 11% 25% 28%
[libx264 @ 0x224be20] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 29% 19% 30%

frame=   64 fps=0.0 q=-1.0 Lsize=      21kB time=00:00:02.58 bitrate=  65.4kbits/s    
video:19kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 8.167657%
[libx264 @ 0x20c4e20] frame I:1     Avg QP:26.84  size:  1181
[libx264 @ 0x20c4e20] frame P:30    Avg QP:24.24  size:   482
[libx264 @ 0x20c4e20] frame B:33    Avg QP:27.56  size:    97
[libx264 @ 0x20c4e20] consecutive B-frames: 10.9% 53.1% 23.4% 12.5%
[libx264 @ 0x20c4e20] mb I  I16..4:  4.1% 71.4% 24.5%
[libx264 @ 0x20c4e20] mb P  I16..4:  0.8% 14.6%  1.2%  P16..4: 30.7% 25.6% 12.5%  0.0%  0.0%    skip:14.5%
[libx264 @ 0x20c4e20] mb B  I16..4:  0.1%  0.9%  0.1%  B16..8: 20.7%  6.4%  1.8%  direct: 3.6%  skip:66.5%  L0:34.8% L1:46.8% BI:18.4%
[libx264 @ 0x20c4e20] 8x8 transform intra:85.1% inter:61.0%
[libx264 @ 0x20c4e20] coded y,uvDC,uvAC intra: 69.4% 68.3% 38.8% inter: 20.8% 31.0% 6.6%
[libx264 @ 0x20c4e20] i16 v,h,dc,p: 53% 20%  7% 20%
[libx264 @ 0x20c4e20] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 28% 19% 38%

frame=   64 fps=0.0 q=-1.0 Lsize=      22kB time=00:00:02.58 bitrate=  68.4kbits/s    
video:20kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 7.610602%
[libx264 @ 0xb98fe0] frame I:1     Avg QP:20.51  size:  1113
[libx264 @ 0xb98fe0] frame P:33    Avg QP:24.99  size:   468
[libx264 @ 0xb98fe0] frame B:30    Avg QP:28.23  size:   110
[libx264 @ 0xb98fe0] consecutive B-frames: 17.2% 56.2% 14.1% 12.5%
[libx264 @ 0xb98fe0] mb I  I16..4:  2.0% 95.9%  2.0%
[libx264 @ 0xb98fe0] mb P  I16..4:  1.1% 11.2%  1.6%  P16..4: 34.4% 26.9% 10.6%  0.0%  0.0%    skip:14.2%
[libx264 @ 0xb98fe0] mb B  I16..4:  0.1%  0.6%  0.0%  B16..8: 25.0%  6.9%  2.2%  direct: 4.4%  skip:60.7%  L0:34.6% L1:46.8% BI:18.6%
[libx264 @ 0xb98fe0] 8x8 transform intra:83.2% inter:65.3%
[libx264 @ 0xb98fe0] coded y,uvDC,uvAC intra: 68.9% 77.2% 43.5% inter: 22.3% 37.5% 7.1%
[libx264 @ 0xb98fe0] i16 v,h,dc,p: 43% 10% 10% 38%
[libx264 @ 0xb98fe0] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 25% 20% 36%  2%  3%  5

  libpostproc    53.  3.100 / 53.  3.100
[mjpeg @ 0x1d03060] Changeing bps to 8
Input #0, avi, from '/data/GaitData/ActivationMap_videos/AGNet/1154450_test_0_trial_2.avi':
  Metadata:
    encoder         : Lavf58.26.101
  Duration: 00:00:02.67, start: 0.000000, bitrate: 378 kb/s
    Stream #0:0: Video: mjpeg (MJPG / 0x47504A4D), yuvj420p(pc, bt470bg/unknown/unknown), 112x112, 362 kb/s, 24 fps, 24 tbr, 24 tbn, 24 tbc
No pixel format specified, yuvj420p for H.264 encoding chosen.
Use -pix_fmt yuv420p for compatibility with outdated media players.
[libx264 @ 0x1d05fe0] using cpu capabilities: MMX2 SSE2Fast SSSE3 SSE4.2 AVX FMA3 AVX2 LZCNT BMI2
[libx264 @ 0x1d05fe0] profile High, level 1.0
[libx264 @ 0x1d05fe0] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 f

...

[libx264 @ 0x1cbffe0] profile High, level 1.0
[libx264 @ 0x1cbffe0] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=3 lookahead_threads=1 sliced_threads=0 nr=0 decimate=1 interlaced=0 bluray_compat=0 constrained_intra=0 bframes=3 b_pyramid=2 b_adapt=1 b_bias=0 direct=1 weightb=1 open_gop=0 weightp=2 keyint=250 keyint_min=24 scenecut=40 intra_refresh=0 rc_lookahead=40 rc=crf mbtree=1 crf=23.0 qcomp=0.60 qpmin=0 qpmax=69 qpstep=4 ip_ratio=1.40 aq=1:1.00
Output #0, mp4, to '/data/GaitData/ActivationMap_videos/AGNet/mp4/7172046_test_1_trial_2.mp4':
  Metadata:
    encoder         : Lavf56.40.101
    Stream #0:0: Video: h264 (libx264) ([33][0][0][0] / 0x0021), yuvj420p(pc), 112x112, q=-1--1, 24 fps, 12288 tbn, 24 tbc
   

frame=   64 fps=0.0 q=-1.0 Lsize=      23kB time=00:00:02.58 bitrate=  74.0kbits/s    
video:22kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 7.067043%
[libx264 @ 0xa1ffe0] frame I:1     Avg QP:21.27  size:  1081
[libx264 @ 0xa1ffe0] frame P:35    Avg QP:25.74  size:   502
[libx264 @ 0xa1ffe0] frame B:28    Avg QP:28.16  size:   107
[libx264 @ 0xa1ffe0] consecutive B-frames: 17.2% 71.9%  4.7%  6.2%
[libx264 @ 0xa1ffe0] mb I  I16..4:  4.1% 91.8%  4.1%
[libx264 @ 0xa1ffe0] mb P  I16..4:  2.0%  9.4%  1.3%  P16..4: 38.0% 26.8% 12.0%  0.0%  0.0%    skip:10.6%
[libx264 @ 0xa1ffe0] mb B  I16..4:  0.2%  0.2%  0.0%  B16..8: 24.6%  7.1%  2.3%  direct: 3.7%  skip:61.8%  L0:32.2% L1:48.1% BI:19.6%
[libx264 @ 0xa1ffe0] 8x8 transform intra:76.6% inter:65.7%
[libx264 @ 0xa1ffe0] coded y,uvDC,uvAC intra: 70.7% 78.4% 47.3% inter: 26.7% 41.2% 8.3%
[libx264 @ 0xa1ffe0] i16 v,h,dc,p: 36% 41%  8% 15%
[libx264 @ 0xa1ffe0] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 24% 20% 32%  3%  2%  6

frame=   64 fps=0.0 q=-1.0 Lsize=      21kB time=00:00:02.58 bitrate=  65.0kbits/s    
video:19kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 8.215224%
[libx264 @ 0x12fefe0] frame I:1     Avg QP:20.51  size:  1034
[libx264 @ 0x12fefe0] frame P:30    Avg QP:24.70  size:   478
[libx264 @ 0x12fefe0] frame B:33    Avg QP:28.16  size:   101
[libx264 @ 0x12fefe0] consecutive B-frames: 10.9% 56.2% 14.1% 18.8%
[libx264 @ 0x12fefe0] mb I  I16..4:  0.0% 100.0%  0.0%
[libx264 @ 0x12fefe0] mb P  I16..4:  1.7% 11.8%  0.9%  P16..4: 35.7% 23.5% 12.0%  0.0%  0.0%    skip:14.4%
[libx264 @ 0x12fefe0] mb B  I16..4:  0.1%  0.6%  0.0%  B16..8: 22.6%  4.9%  1.1%  direct: 4.5%  skip:66.2%  L0:33.5% L1:50.4% BI:16.1%
[libx264 @ 0x12fefe0] 8x8 transform intra:85.2% inter:68.3%
[libx264 @ 0x12fefe0] coded y,uvDC,uvAC intra: 69.5% 76.0% 36.2% inter: 21.4% 35.1% 7.0%
[libx264 @ 0x12fefe0] i16 v,h,dc,p: 33% 26% 22% 19%
[libx264 @ 0x12fefe0] i8 v,h,dc,ddl,ddr,vr,hd,vl,hu: 31% 17% 34

[libx264 @ 0x2213fe0] using cpu capabilities: MMX2 SSE2Fast SSSE3 SSE4.2 AVX FMA3 AVX2 LZCNT BMI2
[libx264 @ 0x2213fe0] profile High, level 1.0
[libx264 @ 0x2213fe0] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=3 lookahead_threads=1 sliced_threads=0 nr=0 decimate=1 interlaced=0 bluray_compat=0 constrained_intra=0 bframes=3 b_pyramid=2 b_adapt=1 b_bias=0 direct=1 weightb=1 open_gop=0 weightp=2 keyint=250 keyint_min=24 scenecut=40 intra_refresh=0 rc_lookahead=40 rc=crf mbtree=1 crf=23.0 qcomp=0.60 qpmin=0 qpmax=69 qpstep=4 ip_ratio=1.40 aq=1:1.00
Output #0, mp4, to '/data/GaitData/ActivationMap_videos/AGNet/mp4/998903_test_1_trial_2.mp4':
  Metadata:
    encoder         : Lavf56.40.101
    Stream #0:0: Video: h264 

[libx264 @ 0xaeae20] profile High, level 1.0
[libx264 @ 0xaeae20] 264 - core 148 r2643 5c65704 - H.264/MPEG-4 AVC codec - Copyleft 2003-2015 - http://www.videolan.org/x264.html - options: cabac=1 ref=3 deblock=1:0:0 analyse=0x3:0x113 me=hex subme=7 psy=1 psy_rd=1.00:0.00 mixed_ref=1 me_range=16 chroma_me=1 trellis=1 8x8dct=1 cqm=0 deadzone=21,11 fast_pskip=1 chroma_qp_offset=-2 threads=3 lookahead_threads=1 sliced_threads=0 nr=0 decimate=1 interlaced=0 bluray_compat=0 constrained_intra=0 bframes=3 b_pyramid=2 b_adapt=1 b_bias=0 direct=1 weightb=1 open_gop=0 weightp=2 keyint=250 keyint_min=24 scenecut=40 intra_refresh=0 rc_lookahead=40 rc=crf mbtree=1 crf=23.0 qcomp=0.60 qpmin=0 qpmax=69 qpstep=4 ip_ratio=1.40 aq=1:1.00
Output #0, mp4, to '/data/GaitData/ActivationMap_videos/AGNet/mp4/am022_test_1_trial_1.mp4':
  Metadata:
    encoder         : Lavf56.40.101
    Stream #0:0: Video: h264 (libx264) ([33][0][0][0] / 0x0021), yuvj420p(pc), 112x112, q=-1--1, 24 fps, 12288 tbn, 24 tbc
    Met

In [10]:
from IPython.display import HTML
HTML("""
<video src="videos/AGNet/mp4/7160698_test_0_trial_0.mp4" width="448" height="448" controls>
</video>
""")